In [ ]:
%matplotlib inline

# Import important modules
import scipy # for linear algebra
import numpy as np # for linear algebra
import networkx as nx # for manipulating graphs
import csv # read in csv files
import matplotlib  # plotting similar to matlab
import matplotlib.pyplot as plt

# The documentation of networkx can be found here
# https://networkx.github.io/documentation/stable

# For a short introduction to networkx see the following 
# https://networkx.github.io/documentation/stable/tutorial/tutorial.html

**Exercise 1 -- TASK 1**

Replicate the ’small-world’ experiment numerically. Start with a regular k-nearest neighbors ring-graph, and then keep adding random links to this graph and see how the clustering coefficient and the diameter behaves as a function of the link-probability.

Reference:
Watts, Duncan J., and Steven H. Strogatz. "Collective dynamics of'small-world'networks." Nature 393.6684 (1998): 440.


In [ ]:
n = 5000
k = 5

G = nx.newman_watts_strogatz_graph(n,k,0)
# compute the (average) clustering coefficient and the average shortest path length
# Make use of networkx functions where possible!
#C0 = 
#L0 = 

for p in np.logspace(-4,-1):
    G = nx.newman_watts_strogatz_graph(n,k,p)
    # compute the clusterinng coefficient and the average path-length 
    # [...]
    
    # and compare it to the value without rewiring
    # [...]
    

# create a plot of your results
plt.figure();
#[...]
    

** Exercise 1 -- TASK 2 **

You have learned about the Barabasi-Albert preferential attachment model in the lectures. Here we will explore it computionally. Use networkx to construct these graph for varying parameters and report on the result you obtain.

In [ ]:
# let's set up our parameters
n = 10000 # network size
m = 30 # intitial network
G = nx.barabasi_albert_graph(n,m)

# plot the degree distribution 

# now vary the parameter m and set it to 50, 100, 200 -- do you see a change?
# Plot your results

# vary the parameter n and change it to 15000, 20000 -- do you observe a change?
# Plot your results

** Exercise 1 -- TASK 3 **

In this exercise you are going to explore another random graph model, the so-called stochastic blockmodel. We will consider a version of the model defined as follows.
We consider an undirected network with n nodes, which are divided into 2 equal sized groups which we name class 1 and class 2. The probability of a link between two nodes is now given by p if the nodes are in the same class, and by q if the nodes are in two different classes.

Your task is to create graphs with varying parameters and use spectral clustering to see whether you can recover the blocks. 


In [ ]:
def permute_array(A,permutation):
    A = A[permutation,:]
    A = A[:,permutation]
    return A

def compare_clustering(true_clustering, inferred_clustering):
    nr_nodes = float(true_clustering.shape[0])
    overlap = np.sum(true_clustering == inferred_clustering)/nr_nodes
    overlap = max(overlap,1-overlap)
    return overlap

# this function allows you to sample from a stochastic blockmodel with varying parameters
def create_block_model_graph(nr_nodes=2000, p=0.01, q=0.001):
    # build the graph from sparse matrices
    A1 =  np.triu(p > np.random.rand(nr_nodes/2,nr_nodes/2),1)
    A1 =  A1 + A1.T
    
    A2 =  np.triu(p > np.random.rand(nr_nodes/2,nr_nodes/2),1)
    A2 =  A2 + A2.T
    
    A3 =  q > np.random.rand(nr_nodes/2,nr_nodes/2)
    
    # final adjacency matrix
    A = 1*np.hstack([np.vstack([A1,A3]),np.vstack([A3.T,A2])])
    
    # original block variables
    true_blocks = np.kron(np.arange(2),np.ones(nr_nodes/2))
    
    # we disguise the true block labels by shuffling!
    permute = np.random.permutation(nr_nodes)
    true_blocks = true_blocks[permute]
    A = permute_array(A,permute)
    
    # create the graph
    G = nx.from_numpy_matrix(A,create_using=nx.Graph())
    
    return G, true_blocks

#To get a feel for how the blockmodel graph looks like, lets visualize it
G, true_blocks = create_block_model_graph()

# first lets have a look at the adjacency matrix where the nodes are shuffled
# and not ordered according to blocks
plt.figure()
A = nx.adjacency_matrix(G)
plt.spy(A,markersize=0.1);

# and now lets look at the re-ordered version -- note that this is the same graph!
plt.figure()
permute2 = np.argsort(true_blocks)
A2 = permute_array(A,permute2)
plt.spy(A2,markersize=0.1);

In [ ]:
# Let's see if we can recover the blocks using spectral clustering

# fix p of probability inside blocks
p = 0.01
n = 2000
nr_samples = 10

# vary q
for q in np.logspace(-4,-2):
    for s in range(nr_samples):
        G, true_blocks = create_block_model_graph(nr_nodes=n,p=p,q=q)
        # use spectral clustering to infer the blocks -- have a look at your previous 
        # homework!
        # [...]
        # record the accuracy of your inference over the specified number of samples
        # i.e. compute the absolute error b/w your spectral cluster labelling and the true labels given in true_blocks
        # [...]

        
# plot your results using an errorbar plot with mean +- one standard deviation
        